In [1]:
import pandas as pd
import numpy as np

import pickle
import matplotlib.pyplot as plt
import seaborn as sns

from feature_engineering import functions
from utils import utils

In [2]:
# Import Christies dataset

df = pd.read_csv('./data/data-1589349272172-non-french-christies.csv')

In [3]:
# assign column names

title_desc_col = 'title'
medium_col = 'details'
dimension_col = 'details'
url_col = 'image_url'


In [4]:
df_transformed_1 = functions.text_based_transformer(df
                                        , medium=medium_col
                                        , dimensions=dimension_col
                                        , title=title_desc_col)

df_transformed_2 = functions.is_drawing(df_transformed_1)

df_transformed_2['long_list_of_things'] = df_transformed_2['details'].apply(lambda x: functions.long_list_of_things(str(x)))

df = df_transformed_2

/Users/katielazell-fairman/.pyenv/versions/3.8.0/lib/python3.8/site-packages/pandas/core/computation/expressions.py:190: UserWarning: evaluating in Python space because the '+' operator is not supported by numexpr for the bool dtype, use '|' instead
  warnings.warn(


In [5]:
# Load model
model_filename = "model_3_DecisionTreeClassifier_v2features.pkl"

with open('./models/'+ model_filename , 'rb') as file:
    model_file = pickle.load(file)

In [6]:
# Check model file
model_file

{'model': DecisionTreeClassifier(ccp_alpha=0.0, class_weight=None, criterion='gini',
                        max_depth=10, max_features=None, max_leaf_nodes=None,
                        min_impurity_decrease=0.0, min_impurity_split=None,
                        min_samples_leaf=1, min_samples_split=5,
                        min_weight_fraction_leaf=0.0, presort='deprecated',
                        random_state=None, splitter='best'),
 'features': ['long_list_of_things',
  'installation_keyword',
  'print_keyword',
  'drawing_paper_word',
  'drawing_keyword',
  'painting_keyword',
  'photo_keyword',
  'has_3dimensions',
  'furniture_keyword',
  'sculpture_keyword',
  'decorative_obj_keyword',
  'decorative_obj_keyword_med',
  'is_drawing'],
 'labels': ['Drawing',
  'Installation',
  'Painting',
  'Photograph',
  'Print',
  'Sculpture',
  'decorative_object',
  'furniture']}

In [7]:
# Asign assets

model = model_file['model']
features = model_file['features']
labels = model_file['labels']

# Check all Model Features Exist

df[features]

long_list_of_things  installation_keyword  print_keyword  \
0                    False                 False          False   
1                     True                 False          False   
2                    False                 False          False   
3                    False                  True          False   
4                    False                 False          False   
...                    ...                   ...            ...   
38926                 True                  True          False   
38927                 True                 False          False   
38928                False                 False          False   
38929                 True                 False          False   
38930                False                 False          False   

       drawing_paper_word  drawing_keyword  painting_keyword  photo_keyword  \
0                   False            False              True          False   
1                    True            False             False           True   
2                   False            False             False          False   
3                   False            False             False          False   
4                   False            False              True          False   
...                   ...              ...               ...            ...   
38926               False             True              True           True   
38927               False            False             False          False   
38928                True            False              True          False   
38929               False             True             False           True   
38930               False            False              True          False   

       has_3dimensions  furniture_keyword  sculpture_keyword  \
0                False              False              False   
1                False              False              False   
2                 True              False              False   
3                 True              False               True   
4                False              False              False   
...                ...                ...                ...   
38926            False              False              False   
38927             True              False               True   
38928            False              False              False   
38929             True              False              False   
38930             True              False              False   

       decorative_obj_keyword  decorative_obj_keyword_med  is_drawing  
0                       False                       False       False  
1                       False                       False        True  
2                       False                       False       False  
3                       False                       False       False  
4                        True                       False       False  
...                       ...                         ...         ...  
38926                   False                       False        True  
38927                   False                       False       False  
38928                   False                       False        True  
38929                   False                       False        True  
38930                   False                       False       False  

[38931 rows x 13 columns]

In [8]:
# Get test results

results = model.predict(df[features])
y_pred = pd.DataFrame(columns=labels
                      , data=results
                      , index=df.index)

# create label for non classified results

y_pred['no_classification'] = y_pred.apply(lambda x: 1 if sum(x) == 0 else 0, axis=1)
x = y_pred.stack()
results = pd.Series(pd.Categorical(x[x!=0].index.get_level_values(1)))

df_classifications=pd.DataFrame(results, columns=['Classification'])

In [9]:
df_classified = df.join(df_classifications)

In [10]:
df_classified

index            sale_date   price  estimate_min  estimate_max  \
0      24173  2010-09-22 00:00:00   16250       15000.0       20000.0   
1      24113  2010-09-22 00:00:00   13750        8000.0       12000.0   
2      24125  2010-09-22 00:00:00   11875       12000.0       18000.0   
3      24126  2010-09-22 00:00:00   47500       25000.0       35000.0   
4      24235  2010-11-03 00:00:00  626500      500000.0      700000.0   
...      ...                  ...     ...           ...           ...   
38926  24105  2010-09-22 00:00:00   80500       40000.0       60000.0   
38927  24107  2010-09-22 00:00:00   11250       10000.0       15000.0   
38928  24132  2010-09-22 00:00:00   74500       30000.0       40000.0   
38929  24109  2010-09-22 00:00:00   25000       10000.0       15000.0   
38930  24110  2010-09-22 00:00:00   47500       30000.0       40000.0   

      currency             artist  \
0         USD   Eberhard Havekost   
1         USD        Vito Acconci   
2         USD       Lucio Fontana   
3         USD       Lynda Benglis   
4         USD        Marc Chagall   
...        ...                ...   
38926     USD             Christo   
38927     USD        Kenny Scharf   
38928     USD    Alexander Calder   
38929     USD       Dario Robleto   
38930     USD      Allan Mccollum   

                                                   title  \
0                                            Untitled \r   
1                                       Changing Title\r   
2                                            Untitled \r   
3                              Untitled (Shady Grove) \r   
4                      Fleurs dans un vase u carreaux \r   
...                                                  ...   
38926  Wrapped Walkways (Project for St. Stephens Gre...   
38927                                       Phorshine \r   
38928                                        Untitled \r   
38929              If We Fly Away, Theyll Fly Away... \r   
38930                                 Perfect Vehicle \r   

                                                    size  \
0                  13 3/8 x 17 3/8 in. (33.9 x 45.4 cm.)   
1                    30 x 14\u00bd in. (76.2 x 36.8 cm.)   
2            5\u00bc x 5 x 4 in. (13.3 x 12.7 x 10.1cm.)   
3      34\u00bd x 19\u00bd x 3\u00be in. (87.6 x 49.5...   
4                      19 5/8 x 16 in. (49.8 x 40.6 cm.)   
...                                                  ...   
38926                      28 x 22 in. (71.1 x 55.8 cm.)   
38927          20 x 14 x 14 in. (50.8 x 35.5 x 35.5 cm.)   
38928               29\u00bd x 43 in. (74.9 x 109.2 cm.)   
38929         24 x 16 x 16 in. (60.9 x 40.6 x 40. 6 cm.)   
38930         78 x 36 x 36 in. (198.1 x 91.4 x 91.4 cm.)   

                                                 details  ... drawing_keyword  \
0      ["signed and dated Havekost DD 97 (on the reve...  ...           False   
1      ["signed, titled and dated Changing Title 1969...  ...           False   
2      ["incised with initials and dated LF 47 (on th...  ...           False   
3      ["signed with initials and numbered LB 282 (on...  ...           False   
4      ["signed Marc Chagall (lower right) \r","oil o...  ...           False   
...                                                  ...  ...             ...   
38926  ["signed and dated CHRISTO 1977 (upper right o...  ...            True   
38927  ["signed, numbered and dated Kenny Scharf 96 3...  ...           False   
38928  ["signed and dated Calder 66 (lower right) \r"...  ...           False   
38929  ["Bone dust, fabric, metal, silver, lead, viny...  ...            True   
38930  ["acrylic enamel on glass-fiber-reinforced con...  ...           False   

      painting_keyword  photo_keyword sculpture_keyword  \
0                 True          False             False   
1                False           True             False   
2                False          False             False   
3                False          Fa

In [11]:
df_cat = df_classified[['index', 'Classification']].groupby('Classification').count().sort_values('index', ascending=False)


In [12]:
# Counts of each category
df_cat

index
Classification          
Painting           17335
Drawing             9590
Sculpture           5725
no_classification   3623
Photograph           798
decorative_object    766
Installation         626
Print                328
furniture            140

In [13]:
## Check out Furniture Examples

clas = 'furniture'
utils.view_images_from_url(df_classified[df_classified['Classification'] == clas]
                     , url_col
                     , subsample=True
                     , sample_size=30
                     , random_state=8)

21782


23196


32203


5117


1872


...

19367


12637


20081


34739


1336


### Some furniture not correct since it depects drawings of furniture

In [15]:
clas = 'Installation'
utils.view_images_from_url(df_classified[df_classified['Classification'] == clas]
                     , url_col
                     , subsample=True
                     , sample_size=30
                     , random_state=0)

22590


17293


28484


18220


28768


...

31014


11723


22059


2295


13781


### Not great for Installation

In [16]:
clas = 'Photograph'
utils.view_images_from_url(df_classified[df_classified['Classification'] == clas]
                     , url_col
                     , subsample=True
                     , sample_size=30
                     , random_state=888)

38888


38124


13918


2365


472


...

23437


12228


8767


18291


14553


In [ ]:
# Pretty good for Photograph

In [17]:
clas = 'decorative_object'
utils.view_images_from_url(df_classified[df_classified['Classification'] == clas]
                     , url_col
                     , subsample=True
                     , sample_size=50
                     , random_state=888)

25425


14095


188


30219


5303


...

24554


38787


20495


34393


37420


### Some false positives due to subject matter of painint/drawing

In [18]:
clas = 'Sculpture'
utils.view_images_from_url(df_classified[df_classified['Classification'] == clas]
                     , url_col
                     , subsample=True
                     , sample_size=50
                     , random_state=888)

2523


6277


32175


21157


3276


...

5851


32466


25526


29623


21928


### Pretty good

In [20]:
clas = 'no_classification'
utils.view_images_from_url(df_classified[df_classified['Classification'] == clas]
                     , url_col
                     , subsample=True
                     , sample_size=50
                     , random_state=888)

16923


34731


31313


17690


27334


...

24912


31516


9421


38716


14822


### Mixed bag

In [21]:
clas = 'Drawing'
utils.view_images_from_url(df_classified[df_classified['Classification'] == clas]
                     , url_col
                     , subsample=True
                     , sample_size=50
                     , random_state=888)

2334


31051


16187


14694


7503


...

14970


30896


28529


34734


8995


### Not that great

In [23]:
clas = 'Painting'
utils.view_images_from_url(df_classified[df_classified['Classification'] == clas]
                     , url_col
                     , subsample=True
                     , sample_size=50
                     , random_state=888)

22578


2443


23917


33300


19886


...

35388


34758


28787


26383


29397


In [24]:
df_classified[df_classified['print_keyword']== True].shape
df_classified.columns

Index(['index', 'sale_date', 'price', 'estimate_min', 'estimate_max',
       'currency', 'artist', 'title', 'size', 'details', 'image_url',
       'timestamp', 'auction_id', 'filename_id', 'filepath', 'filename',
       'long_list_of_things', 'installation_keyword', 'print_keyword',
       'drawing_paper_word', 'drawing_keyword', 'painting_keyword',
       'photo_keyword', 'sculpture_keyword', 'decorative_obj_keyword_med',
       'has_3dimensions', 'furniture_keyword', 'decorative_obj_keyword',
       'is_drawing', 'Classification'],
      dtype='object')

In [25]:
import shutil

def copy_image_to_category_dir(df, category, transfer=False):
    filepath = '/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/'
    target_dir = '/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/'

    for x, y in df['image_url'].items():
        try: 
            dir_ = y.split('/')[-3]
            file = y.split('/')[-1]
            target = target_dir + category + "/" + file
            original = filepath + dir_ + '/' + file
            if transfer:
                shutil.copyfile(original, target)
            print(original)
            print(target)
            print("")
        except:
            print("error")


In [26]:
## Transfer Photographs 


df_photo = df_classified[(df_classified['Classification'] == 'Photograph')
                 & (df_classified['photo_keyword'] == True)]


copy_image_to_category_dir(df_photo, 'photograph', transfer=False)

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2010/2010_NYR_02341_0131_000(catherine_opie_alistair_fate).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/2010_NYR_02341_0131_000(catherine_opie_alistair_fate).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2010/2010_NYR_02341_0134_000(thomas_struth_kunsthistorisches_museum_iii_vienna).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/2010_NYR_02341_0134_000(thomas_struth_kunsthistorisches_museum_iii_vienna).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2010/2010_NYR_02341_0188_000(richard_prince_untitled).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/2010_NYR_02341_0188_000(richard_prince_untitled).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_coll

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2012/2012_DUB_08058_0145_000(reza_aramesh_action_42_fatah_loyalists_at_the_erez_crossing_in_norther).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/2012_DUB_08058_0145_000(reza_aramesh_action_42_fatah_loyalists_at_the_erez_crossing_in_norther).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2013/2013_NYR_02686_0092_000(vivan_sundaram_re-take_of_amrita).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/2013_NYR_02686_0092_000(vivan_sundaram_re-take_of_amrita).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2014/2014_CKS_01510_0031_000(andreas_gursky_singapore_borse_2).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/2014_CKS_01510_0031_000(andreas_gursky_singapore

In [28]:
## Transfer Drawing Examples

df_drawing = df_classified[(df_classified['Classification'] == 'Drawing')
              & (df_classified['drawing_paper_word'] == True)
              & (df_classified['painting_keyword'] == False)]


utils.view_images_from_url(df_drawing
                     , url_col
                     , subsample=True
                     , sample_size=50
                     , random_state=8)

print(df_drawing.shape)

2679


15939


26473


16505


12842


...

18143


1672


2216


38676


(2924, 30)


In [91]:
copy_image_to_category_dir(df_drawing, 'drawing', transfer=True)

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2010/2010_NYR_02341_0091_000(vito_acconci_vito_acconci).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2010_NYR_02341_0091_000(vito_acconci_vito_acconci).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2010/2010_NYR_02341_0120_000(marc_quinn_mothership).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2010_NYR_02341_0120_000(marc_quinn_mothership).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2010/2010_NYR_02353_0112_000(aristide_maillol_erotique).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2010_NYR_02353_0112_000(aristide_maillol_erotique).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2010/2010_NYR_02341_0151_000(david_hockney_portr

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2011/2011_NYR_02424_0559_000(francis_newton_souza_untitled).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2011_NYR_02424_0559_000(francis_newton_souza_untitled).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2011/2011_NYR_02424_0510_000(abdur_rahman_chughtai_duptta).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2011_NYR_02424_0510_000(abdur_rahman_chughtai_duptta).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2011/2011_NYR_02424_0512_000(francis_newton_souza_untitled_untitled).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2011_NYR_02424_0512_000(francis_newton_souza_untitled_untitled).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2011/2011_CSK_05452_0080_000(antony_gormley_untitled).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2011_CSK_05452_0080_000(antony_gormley_untitled).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2011/2011_CSK_05452_0095_000(david_hockney_bob_aboard_the_france).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2011_CSK_05452_0095_000(david_hockney_bob_aboard_the_france).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2011/2011_CSK_05452_0120_000(enzo_cucchi_untitled).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2011_CSK_05452_0120_000(enzo_cucchi_untitled).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2011/2011_CSK_05452_0146_000(ellsw

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2012/2012_CSK_04420_0174_000(tamara_de_lempicka_tete_de_tadeusz).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2012_CSK_04420_0174_000(tamara_de_lempicka_tete_de_tadeusz).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2011/2011_CKS_07991_0201_000(elizabeth_peyton_the_steins_collect_and_flowers).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2011_CKS_07991_0201_000(elizabeth_peyton_the_steins_collect_and_flowers).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2011/2011_CKS_07991_0208_000(richard_serra_transversal_1).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2011_CKS_07991_0208_000(richard_serra_transversal_1).jpg

/Users/katielazell-fairman/Desktop/Projects/Mo

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2012/2012_NYR_02555_0131_000(henri_matisse_marocain_de_trois-quarts).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2012_NYR_02555_0131_000(henri_matisse_marocain_de_trois-quarts).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2012/2012_NYR_02555_0144_000(paul_klee_madchen_mit_puppe).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2012_NYR_02555_0144_000(paul_klee_madchen_mit_puppe).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2012/2012_NYR_02555_0146_000(pablo_picasso_tete_et_buste_dhomme_sans_titre).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2012_NYR_02555_0146_000(pablo_picasso_tete_et_buste_dhomme_sans_titre).jpg

/Users/katielazell-fairman/Desktop/Project

...

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2014/2014_CKS_01532_0006_000(pablo_picasso_deux_nus_couches).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2014_CKS_01532_0006_000(pablo_picasso_deux_nus_couches).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2014/2014_CKS_01531_0064_000(mukul_dey_cotton_street_barrabazar_calcutta_nandalal_boses_birthplace).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2014_CKS_01531_0064_000(mukul_dey_cotton_street_barrabazar_calcutta_nandalal_boses_birthplace).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2014/2014_CKS_01533_0150_000(oskar_schlemmer_im_holzhaus).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2014_CKS_01533_0150_000(oskar_schlemmer_im_holzhaus).jpg

/Users/kat

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2006/2006_CSK_05010_0131_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2006_CSK_05010_0131_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2007/2007_NYR_01905_0314_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2007_NYR_01905_0314_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2006/2006_CKS_07247_0139_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2006_CKS_07247_0139_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2014/2014_NYR_02892_0157_000(agnes_martin_untitled).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2014_NYR_02892_0157_000(ag

error
/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2008/2008_NYR_01975_0012_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2008_NYR_01975_0012_000().jpg

error
/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2008/2008_NYR_01970_0260_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2008_NYR_01970_0260_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2008/2008_NYR_01970_0261_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2008_NYR_01970_0261_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2008/2008_NYR_01970_0262_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2008_NYR_01970_0262_000().jpg

/Use

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2008/2008_NYR_02093_0028_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2008_NYR_02093_0028_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2008/2008_NYR_02093_0249_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2008_NYR_02093_0249_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2008/2008_NYR_02093_0135_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2008_NYR_02093_0135_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2008/2008_NYR_02093_0164_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2008_NYR_02093_0164_000().jpg

/Users/katielaze

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2009/2009_CKS_07703_0167_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2009_CKS_07703_0167_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2009/2009_CKS_07703_0117_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2009_CKS_07703_0117_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2009/2009_CKS_07703_0138_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2009_CKS_07703_0138_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2009/2009_CKS_07703_0164_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/drawing/2009_CKS_07703_0164_000().jpg

/Users/katielaze

In [29]:
# Transfer Painting Examples

df_painting = df_classified[(df_classified['Classification'] == 'Painting')
              & (df_classified['painting_keyword'] == True)].sample(5000, random_state=8) # Limit to max 5000

utils.view_images_from_url(df_painting
                     , url_col
                     , subsample=True
                     , sample_size=50
                     , random_state=9)


print(df_painting.shape)

19742


10551


38725


20055


12361


...

5246


4248


7881


21403


(5000, 30)


In [30]:
copy_image_to_category_dir(df_painting, 'painting', transfer=False)

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2008/2008_NYR_02049_0273_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/painting/2008_NYR_02049_0273_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2015/2015_HGK_03415_0104_000(yuan_yuan_steam_room_iii).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/painting/2015_HGK_03415_0104_000(yuan_yuan_steam_room_iii).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2007/2007_CKS_07405_0389_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/painting/2007_CKS_07405_0389_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2006/2006_NYR_01655_0042_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/pain

/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/painting/2014_CKS_01545_0077_000(john_atkinson_grimshaw_the_gossips_bonchurch_isle_of_wight).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2012/2012_CKS_06766_0005_000(brett_cody_rogers_untitled).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/painting/2012_CKS_06766_0005_000(brett_cody_rogers_untitled).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2011/2011_DUB_07933_0011_000(paul_guiragossian_allegresse).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/painting/2011_DUB_07933_0011_000(paul_guiragossian_allegresse).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2006/2006_CKS_07296_0407_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/trainin


/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2016/2016_HGK_12516_0178_000(mitsuru_watanabe_naoko_bathing_in_the_woods_of_rousseau).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/painting/2016_HGK_12516_0178_000(mitsuru_watanabe_naoko_bathing_in_the_woods_of_rousseau).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2008/2008_NYR_02046_0135_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/painting/2008_NYR_02046_0135_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2012/2012_NYR_02597_0019_000(richard_diebenkorn_ocean_park_48).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/painting/2012_NYR_02597_0019_000(richard_diebenkorn_ocean_park_48).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2013/2013_CK


/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2016/2016_HGK_12516_0138_000(zeng_fanzhi_mao).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/painting/2016_HGK_12516_0138_000(zeng_fanzhi_mao).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2014/2014_DUB_01230_0003_000(youssef_kamel_untitled).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/painting/2014_DUB_01230_0003_000(youssef_kamel_untitled).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2015/2015_NYR_03787_0129_000(samuel_colman_becalmed_in_the_highlands).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/painting/2015_NYR_03787_0129_000(samuel_colman_becalmed_in_the_highlands).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2012/2012_CKS_05472_0450_000(mauri

/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/painting/2007_CKS_07406_0030_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2011/2011_NYR_02479_0321_000(leonard-tsuguharu_foujita_le_medaillon).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/painting/2011_NYR_02479_0321_000(leonard-tsuguharu_foujita_le_medaillon).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2016/2016_NYR_12123_0048_000(hans_hofmann_morning_light).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/painting/2016_NYR_12123_0048_000(hans_hofmann_morning_light).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2017/2017_NYR_14183_0012A_000(pablo_picasso_femme_assise_robe_bleue).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/trainin


/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2008/2008_CKS_07599_0041_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/painting/2008_CKS_07599_0041_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2006/2006_CSK_04055_0185_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/painting/2006_CSK_04055_0185_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2006/2006_CKS_07296_0494_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/painting/2006_CKS_07296_0494_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2012/2012_NYR_02599_0596_000(lee_ufan_from_line).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/painting/2012_NYR_02599_0596_000(

/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/painting/2006_NYR_01704_0233_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2011/2011_NYR_02439_0398_000(andre_masson_la_route_de_tholonet).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/painting/2011_NYR_02439_0398_000(andre_masson_la_route_de_tholonet).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2017/2017_CKS_13488_0530_000(albert_marquet_le_cercle_nautique_marseille).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/painting/2017_CKS_13488_0530_000(albert_marquet_le_cercle_nautique_marseille).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2007/2007_NYR_01832_0248_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/paintin

In [32]:
# Transfer Sculpture Examples

df_sculpture = df_classified[(df_classified['Classification'] == 'Sculpture')
              & (df_classified['installation_keyword'] == False)
              & (df_classified['painting_keyword'] == False)]

utils.view_images_from_url(df_sculpture
                     , url_col
                     , subsample=True
                     , sample_size=50
                     , random_state=9)


print(df_sculpture.shape)

5678


10564


23466


10925


6752


...

8390


27841


13631


2207


(3284, 30)


In [34]:
copy_image_to_category_dir(df_sculpture, '3D_object', transfer=True)

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2010/2010_NYR_02341_0107_000(lucio_fontana_untitled).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2010_NYR_02341_0107_000(lucio_fontana_untitled).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2010/2010_NYR_02341_0105_000(bryan_hunt_seated_caryatid).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2010_NYR_02341_0105_000(bryan_hunt_seated_caryatid).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2010/2010_NYR_02341_0112_000(deborah_butterfield_untitled).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2010_NYR_02341_0112_000(deborah_butterfield_untitled).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2010/2010_NYR_02341_0145_000(rob

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2011/2011_NYR_02421_0103_000(thomas_scheibitz_star).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2011_NYR_02421_0103_000(thomas_scheibitz_star).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2011/2011_NYR_02421_0125_000(matthew_barney_a_pele_da_lamina).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2011_NYR_02421_0125_000(matthew_barney_a_pele_da_lamina).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2011/2011_NYR_02421_0199_000(sol_lewitt_nine_pyramids_on_a_nine_part_grid).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2011_NYR_02421_0199_000(sol_lewitt_nine_pyramids_on_a_nine_part_grid).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2011/2011_NYR_02482_0230_000(mike_kelley_arena_11_d5495764).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2011_NYR_02482_0230_000(mike_kelley_arena_11_d5495764).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2011/2011_NYR_02482_0218_000(thomas_houseago_midnight_mask_iii).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2011_NYR_02482_0218_000(thomas_houseago_midnight_mask_iii).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2011/2011_NYR_02482_0244_000(charles_ledray_promised_land).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2011_NYR_02482_0244_000(charles_ledray_promised_land).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2011

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2011/2011_CKS_07991_0305_000(jaume_plensa_tel_aviv_man_xi).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2011_CKS_07991_0305_000(jaume_plensa_tel_aviv_man_xi).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2011/2011_CKS_07991_0383_000(thomas_ruff_18h20m_-25).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2011_CKS_07991_0383_000(thomas_ruff_18h20m_-25).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2012/2012_CSK_06240_0170_000(auguste_rodin_hanako_type_e_masque).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2012_CSK_06240_0170_000(auguste_rodin_hanako_type_e_masque).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2012/2012_NYR_02

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2012/2012_NYR_02582_0233_000(avner_ben-gal_tsunami).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2012_NYR_02582_0233_000(avner_ben-gal_tsunami).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2012/2012_NYR_02582_0225_000(larry_rivers_chinese_information).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2012_NYR_02582_0225_000(larry_rivers_chinese_information).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2012/2012_NYR_02582_0226_000(anthony_burdin_voodoo_vox_tour_2000).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2012_NYR_02582_0226_000(anthony_burdin_voodoo_vox_tour_2000).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2012/201

...

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2007/2007_NYR_01835_0277_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2007_NYR_01835_0277_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2007/2007_NYR_01872_0035_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2007_NYR_01872_0035_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2008/2008_NYR_01994_0036_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2008_NYR_01994_0036_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2006/2006_CSK_05008_0108_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2006_CSK_05008_0108_000().jpg

/Users/k

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2007/2007_CKS_07405_0424_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2007_CKS_07405_0424_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2007/2007_CKS_07405_0425_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2007_CKS_07405_0425_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2007/2007_CKS_07405_0426_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2007_CKS_07405_0426_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2007/2007_CKS_07405_0496_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2007_CKS_07405_0496_000().jpg

/Users/k

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2008/2008_NYR_01995_0337_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2008_NYR_01995_0337_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2008/2008_NYR_01995_0340_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2008_NYR_01995_0340_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2008/2008_NYR_01995_0396_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2008_NYR_01995_0396_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2008/2008_NYR_01997_0029_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2008_NYR_01997_0029_000().jpg

/Users/k

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2008/2008_NYR_02048_0017_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2008_NYR_02048_0017_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2008/2008_NYR_02049_0126_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2008_NYR_02049_0126_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2008/2008_NYR_02049_0212_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2008_NYR_02049_0212_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2008/2008_NYR_02049_0282_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2008_NYR_02049_0282_000().jpg

/Users/k

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2008/2008_DUB_07674_0062_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2008_DUB_07674_0062_000().jpg

error
/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2009/2009_NYR_02127_0005_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2009_NYR_02127_0005_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2009/2009_CKS_07701_0011_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2009_CKS_07701_0011_000().jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2009/2009_CKS_07701_0033_000().jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2009_CKS_07701_0033_000().jpg

/U

In [41]:
# Transfer Furniture Examples

df_furniture = df_classified[(df_classified['Classification'] == 'furniture')
              & (df_classified['installation_keyword'] == False)
              & (df_classified['painting_keyword'] == False)
              & (df_classified['is_drawing'] == False)]

utils.view_images_from_url(df_furniture
                     , url_col
                     , subsample=True
                     , sample_size=50
                     , random_state=10)


print(df_furniture.shape)

16762


1956


22857


15189


12413


...

36540


37121


4626


31345


(59, 30)


In [40]:
copy_image_to_category_dir(df_furniture, '3D_object', transfer=True)

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2011/2011_NYR_02424_0631_000(francis_newton_souza_untitled_untitled_untitled).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2011_NYR_02424_0631_000(francis_newton_souza_untitled_untitled_untitled).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2011/2011_NYR_02439_0416_000(diego_giacometti_table_grecque_modele_carre).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2011_NYR_02439_0416_000(diego_giacometti_table_grecque_modele_carre).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2011/2011_NYR_02442_0418_000(marina_abramovic_chair_for_non-human_use).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2011_NYR_02442_0418_000(marina_abramovic_chair_for_non-human_use).j

In [43]:
# Transfer Decorative Objects

df_dec_obj = df_classified[(df_classified['Classification'] == 'decorative_object')
              & (df_classified['installation_keyword'] == False)
              & (df_classified['painting_keyword'] == False)
              & (df_classified['is_drawing'] == False)]

utils.view_images_from_url(df_dec_obj
                     , url_col
                     , subsample=True
                     , sample_size=50
                     , random_state=10)


print(df_dec_obj.shape)

23343


8360


6815


2576


25494


...

10897


5696


6828


23173


(426, 30)


In [44]:
copy_image_to_category_dir(df_dec_obj, '3D_object', transfer=True)

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2010/2010_NYR_02341_0109_000(george_rickey_one_up_one_down_gimbaled-wall).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2010_NYR_02341_0109_000(george_rickey_one_up_one_down_gimbaled-wall).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2010/2010_NYR_02341_0161_000(jennifer_bartlett_summer).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2010_NYR_02341_0161_000(jennifer_bartlett_summer).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2010/2010_NYR_02354_0315_000(auguste_rodin_jeunesse_triomphante).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2010_NYR_02354_0315_000(auguste_rodin_jeunesse_triomphante).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_colle

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2013/2013_CKS_01133_0311_000(pablo_picasso_grand_vase_aux_femmes_voilees).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2013_CKS_01133_0311_000(pablo_picasso_grand_vase_aux_femmes_voilees).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2013/2013_CKS_01133_0317_000(after_a_design_by_diego_giacometti_la_promenade_des_amis).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2013_CKS_01133_0317_000(after_a_design_by_diego_giacometti_la_promenade_des_amis).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2013/2013_NYR_02787_0554_000(sean_scully_atlas_walls).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2013_NYR_02787_0554_000(sean_scully_atlas_walls).jpg

/Users/katie

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2013/2013_CSK_08257_0251_000(pablo_picasso_visage_no_179).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2013_CSK_08257_0251_000(pablo_picasso_visage_no_179).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2014/2014_CSK_05930_0114_000(sir_eduardo_paolozzi_ra_eluz).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2014_CSK_05930_0114_000(sir_eduardo_paolozzi_ra_eluz).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2014/2014_NYR_02824_0281_000(ibram_lassaw_pendant).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2014_NYR_02824_0281_000(ibram_lassaw_pendant).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2016/2016_NYR_12153_0144_000(otto_

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2014/2014_NYR_03473_0529_000(massimo_micheluzzi_a_vase_2013).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2014_NYR_03473_0529_000(massimo_micheluzzi_a_vase_2013).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2013/2013_NYR_02683_0051_000(barry_mcgee_venice_wall).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2013_NYR_02683_0051_000(barry_mcgee_venice_wall).jpg

/Users/katielazell-fairman/Desktop/Projects/MoMa_collection/Data/images/2013/2013_CSK_08257_0005_000(fernand_leger_and_roland_brice_nature_morte_aux_feuilles_et_fruit).jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/3D_object/2013_CSK_08257_0005_000(fernand_leger_and_roland_brice_nature_morte_aux_feuilles_et_fruit).jpg

/Users/katielazell-f

### Category Counts 

* 3D object - 5254
* drawing - 2820
* painting - 4837
* photographs - 472

In [48]:
# Import MoMA dataset

df_moma = pd.read_csv('data/data-1589133901203-moma-artwork-data.csv')

In [49]:
df_moma_photo = df_moma[df_moma['Classification'] == "Photograph"]
df_moma_photo.shape

(15890, 31)

In [59]:
utils.view_images_from_url(df_moma_photo.sample(5000, random_state=8)
                     , 'ThumbnailURL'
                     , subsample=True
                     , sample_size=50
                     , random_state=10)

18932


58128


14078


68107


63807


...

13274


15271


18203


14678


16119


In [52]:
df_moma_photo.columns

Index(['index', 'Title', 'Artist', 'ConstituentID', 'ArtistBio', 'Nationality',
       'BeginDate', 'EndDate', 'Gender', 'Date', 'Medium', 'Dimensions',
       'CreditLine', 'AccessionNumber', 'Classification', 'Department',
       'DateAcquired', 'Cataloged', 'ObjectID', 'URL', 'ThumbnailURL',
       'Circumference_cm', 'Depth_cm', 'Diameter_cm', 'Height_cm', 'Length_cm',
       'Weight_kg', 'Width_cm', 'SeatHeight_cm', 'Duration_sec', 'updated_at'],
      dtype='object')

In [61]:
# check sample 
for x in df_moma_photo['ThumbnailURL'].sample(40):
    print(x)

http://www.moma.org/media/W1siZiIsIjM0NTUzOCJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=fc8d97794bf9e68f
http://www.moma.org/media/W1siZiIsIjMwMTMwNCJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=1b26099184a50916
http://www.moma.org/media/W1siZiIsIjMxODEwMSJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=253557076d2d4cd8
http://www.moma.org/media/W1siZiIsIjMxODEwMiJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=4230f841c70288a2
http://www.moma.org/media/W1siZiIsIjI4NjE4MiJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=06de80692ab750c8
http://www.moma.org/media/W1siZiIsIjI4NjE4MyJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=7041535f534d07be
http://www.moma.org/media/W1siZiIsIjIyNjAxNSJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=bfe5fbad15d05467
http://www.moma.org/media/W1siZiIsIjI4MzU3MCJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=9

http://www.moma.org/media/W1siZiIsIjI5OTQ2NiJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=d9dc6a7edd2db6a1
http://www.moma.org/media/W1siZiIsIjI4NDk5NyJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=34a31e4dbf765b44
http://www.moma.org/media/W1siZiIsIjM5MzQxNiJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=dc18c2c52990d477
http://www.moma.org/media/W1siZiIsIjI4Mjk3OSJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=282f08c23ed50080
http://www.moma.org/media/W1siZiIsIjMwMDM3MSJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=c522c62719acd3ef
http://www.moma.org/media/W1siZiIsIjI4NTQwMyJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=0dbef84f5a1fb97b
http://www.moma.org/media/W1siZiIsIjI4Mzg5OSJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=fa689d1e3ce0fd99
http://www.moma.org/media/W1siZiIsIjI3NDkzMCJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=0

http://www.moma.org/media/W1siZiIsIjI1ODcxNiJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=9fd3a1010ea2337e
http://www.moma.org/media/W1siZiIsIjE5Mjk5MyJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=bb3c0365451aa15f
http://www.moma.org/media/W1siZiIsIjE2MjQiXSxbInAiLCJjb252ZXJ0IiwiLXJlc2l6ZSAzMDB4MzAwXHUwMDNlIl1d.jpg?sha=eed0ccbff6853a42
http://www.moma.org/media/W1siZiIsIjE5MzM1NyJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=9e8a7bd3a3e7827f
http://www.moma.org/media/W1siZiIsIjE5MzM1OCJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=0b45054a8ffbc989
http://www.moma.org/media/W1siZiIsIjE4NjgxNyJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=364f03ddd6be7b44
http://www.moma.org/media/W1siZiIsIjIwNzcwOCJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=f1e851d1b3d09c25
http://www.moma.org/media/W1siZiIsIjE4NjgxOCJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=de0c

http://www.moma.org/media/W1siZiIsIjIzOTU0MSJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=7b9d193e9acba6a0
http://www.moma.org/media/W1siZiIsIjE4ODU5NSJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=7d088a656a258efc
http://www.moma.org/media/W1siZiIsIjQ0NDkzNyJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=1c70889c91f59b15
http://www.moma.org/media/W1siZiIsIjIzMzk2OSJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=434f4cbe20ce325b
http://www.moma.org/media/W1siZiIsIjE4NjcyMyJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=323d5b1583474c3c
http://www.moma.org/media/W1siZiIsIjEzOTg2NCJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=b803ec86c2153a99
http://www.moma.org/media/W1siZiIsIjE4NjQ5MSJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=631a69789aa2b8d4
http://www.moma.org/media/W1siZiIsIjE1Nzk5NiJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=9

http://www.moma.org/media/W1siZiIsIjE5MDcwNCJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=14b4cd45ad7f4cb1
http://www.moma.org/media/W1siZiIsIjE5MDcwNSJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=dda16e8c344be7d5
http://www.moma.org/media/W1siZiIsIjIwOTI5NiJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=af7be50a8e57b7ae
http://www.moma.org/media/W1siZiIsIjE5MDcwNyJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=2050a630082e8682
http://www.moma.org/media/W1siZiIsIjE5MDcwOCJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=c7f3851309c975d5
http://www.moma.org/media/W1siZiIsIjk3NzQiXSxbInAiLCJjb252ZXJ0IiwiLXJlc2l6ZSAzMDB4MzAwXHUwMDNlIl1d.jpg?sha=6284842b3c4c4064
http://www.moma.org/media/W1siZiIsIjE5MDcwOSJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=788df77d2487aec7
http://www.moma.org/media/W1siZiIsIjk3NzkiXSxbInAiLCJjb252ZXJ0IiwiLXJlc2l6ZSAzMDB4MzAwXHUwMDNlIl1d.jpg?sha=68e54b9

http://www.moma.org/media/W1siZiIsIjIwMTY5MiJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=e5f7cc840ae0ca6e
http://www.moma.org/media/W1siZiIsIjI4OTUwNiJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=9aa2f5c00372d43e
http://www.moma.org/media/W1siZiIsIjE5Mjg2NSJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=a3642b18421e57b6
http://www.moma.org/media/W1siZiIsIjE5MDc0MSJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=ac92134a93f5d8f6
http://www.moma.org/media/W1siZiIsIjE5MDY5NiJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=05b285a9d4b7851f
http://www.moma.org/media/W1siZiIsIjE5MDcxOSJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=852550ed22004a10
http://www.moma.org/media/W1siZiIsIjE5Mjk2MCJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=f1844b5976c9abc2
http://www.moma.org/media/W1siZiIsIjE5MjkzOCJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=d

http://www.moma.org/media/W1siZiIsIjI2ODAxOCJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=5e38f18ef238d4fe
http://www.moma.org/media/W1siZiIsIjI2ODAxOSJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=c8c826a06553b4eb
http://www.moma.org/media/W1siZiIsIjI2NTYwNyJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=9096b121a9941a73
http://www.moma.org/media/W1siZiIsIjI2NTYwNiJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=8c4bb5cee4ffddc3
http://www.moma.org/media/W1siZiIsIjI2NTYwNSJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=69ebc243b3b41308
http://www.moma.org/media/W1siZiIsIjI2ODAzNCJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=d1dd7e7c6231ba89
http://www.moma.org/media/W1siZiIsIjI1OTEzMyJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=a8fe80c8c5a7db86
http://www.moma.org/media/W1siZiIsIjQ1NjkwNSJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=8

http://www.moma.org/media/W1siZiIsIjM5NzY0MSJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=f51592635905eae9
http://www.moma.org/media/W1siZiIsIjM5NzY0MiJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=e3c47f4b394ab194
http://www.moma.org/media/W1siZiIsIjM5MzEzMSJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=c11faad481725eba
http://www.moma.org/media/W1siZiIsIjM5MzEzNCJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=00c56279fb12540a
http://www.moma.org/media/W1siZiIsIjM5NzY0MyJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=0473c08cb5a75ff2
http://www.moma.org/media/W1siZiIsIjQzMjcxOSJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=95458950242f4f90
http://www.moma.org/media/W1siZiIsIjM5MzEzMiJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=91c453183e30d1c2
http://www.moma.org/media/W1siZiIsIjM5MzEzMyJdLFsicCIsImNvbnZlcnQiLCItcmVzaXplIDMwMHgzMDBcdTAwM2UiXV0.jpg?sha=8

In [76]:
from PIL import Image
import requests
from io import BytesIO

#Download images

# for img in df_moma_photo['ThumbnailURL'].sample(5000, random_state=20)[3000:4000]:
#     dir_ = target_dir = '/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/'
#     category = 'photograph'
#     filename = img.split("sha=")[-1]
    
#     response = requests.get(img)
#     img = Image.open(BytesIO(response.content))
#     img.save(dir_ + category + "/" +filename + ".jpg", 'jpeg')
#     print(dir_ + category + "/" +filename + ".jpg")

/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/b673acbe58e02f1a.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/ebbe26e2339c6cb4.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/6095b8ed61264e10.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/1ce7b96079d4e8e7.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/8568fe6b5e86ec46.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/65b5da6ef0d0645d.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/89d71990eb37d397.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classi

/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/325174d55580d67a.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/a8b1a590d1067941.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/5b4960907fe19e14.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/8fe4c1387924c353.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/0bcaa6c0e0fe31c0.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/73d7221844fdfc60.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/0ea04889e60db7e7.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classi

/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/f4fef59f3b1d0840.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/0475d94a359f3010.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/ec4d793e7d600ebf.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/1b0dd22155e784c3.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/9251a9e77d772890.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/44b593045273b78d.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/43c0c78efa9da39b.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classi

/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/1e4864e279c0d035.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/7e13b1e3d9113b6b.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/d00fa511474406db.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/dd06de581e94e07f.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/4b2a4d0f111bddaf.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/503eea561502afd2.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/86effe9e597512e2.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classi

/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/9382cc07c5367ca5.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/e7220b190d3838c4.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/552b2ba5730f3f3c.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/fd5e1fb02322a07f.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/d7102cb4cd497ae9.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/5a206aaa8e5d658a.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/b6e2fe6d23066ac1.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classi

...

/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/cc754765afbc0948.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/3958ebb16ef96d33.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/58fbcc717f371617.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/ecba8398adb446e2.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/a5081dc284571b86.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/d9f0ecfa88ac6b86.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/45d66b7498daed84.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classi

/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/46e6e24bb55b9bfb.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/c0af4f9ff5e03510.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/25e087d2a6619357.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/58a917ae224afe96.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/3ff59b9675c69e21.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/4d87e3dfe37eb4f8.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/7b16d2ac37e11248.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classi

/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/a9c210252023574a.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/36a941e74a931732.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/a01adb64b4f588e5.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/d6e7d957871a9ed6.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/37e7dc115fa8e91b.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/0290045f086b4c33.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/87937348feed21d3.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classi

/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/a724c7f62aa34eb1.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/c3e5197c6d160090.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/b18841d8187e15a8.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/94c9dffdef36ff3f.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/c77367de22c8427a.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/417b50954af61912.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/a8b50e2979734cf3.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classi

/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/5048304166558970.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/71f13779ed861d45.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/0f0760746a296519.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/4237f44906d29208.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/38499ba597ad2ec7.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/9dee95f14dbc6198.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classifier/data/training_data/photograph/23eaa28262866f7b.jpg
/Users/katielazell-fairman/Documents/artluxe/feasibility_testing/item_classi

In [77]:
df_moma_draw = df_moma[df_moma['Classification'] == "Drawing"]
df_moma_draw.shape

(9525, 31)

In [78]:
utils.view_images_from_url(df_moma_draw.sample(5000, random_state=8)
                     , 'ThumbnailURL'
                     , subsample=True
                     , sample_size=50
                     , random_state=10)

35714


41985


9929


40710


38656


...

37259


61356


39374


11435


11804
